In [2]:

import os
import re
from tqdm import tqdm


def bracket_filter(sentence, mode='phonetic'):
    new_sentence = str()

    if mode == 'phonetic':
        flag = False

        for ch in sentence:
            if ch == '(' and flag is False:
                flag = True
                continue
            if ch == '(' and flag is True:
                flag = False
                continue
            if ch != ')' and flag is False:
                new_sentence += ch

    elif mode == 'spelling':
        flag = True

        for ch in sentence:
            if ch == '(':
                continue
            if ch == ')':
                if flag is True:
                    flag = False
                    continue
                else:
                    flag = True
                    continue
            if ch != ')' and flag is True:
                new_sentence += ch

    else:
        raise ValueError("Unsupported mode : {0}".format(mode))

    return new_sentence


def special_filter(sentence, mode='phonetic', replace=None):
    SENTENCE_MARK = ['?', '!', '.']
    NOISE = ['o', 'n', 'u', 'b', 'l']
    EXCEPT = ['/', '+', '*', '-', '@', '$', '^', '&', '[', ']', '=', ':', ';', ',']

    new_sentence = str()
    for idx, ch in enumerate(sentence):
        if ch not in SENTENCE_MARK:
            if idx + 1 < len(sentence) and ch in NOISE and sentence[idx + 1] == '/':
                continue

        if ch == '#':
            new_sentence += '샾'

        elif ch == '%':
            if mode == 'phonetic':
                new_sentence += replace
            elif mode == 'spelling':
                new_sentence += '%'

        elif ch == '\n':
            continue
        elif ch not in EXCEPT:
            new_sentence += ch

    pattern = re.compile(r'\s\s+')
    new_sentence = re.sub(pattern, ' ', new_sentence.strip())
    return new_sentence


def sentence_filter(raw_sentence, mode, replace=None):
    return special_filter(bracket_filter(raw_sentence, mode), mode, replace)

In [3]:
import json

file_path = 'news_manifest.json'
data = []

old_prefix = '/shared/home/milab/users/kskim/dataset/138.뉴스_대본_및_앵커_음성_데이터'
new_prefix = '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터'

with open(file_path, 'r', encoding='utf-8') as f:
    for line in f:
        if line.strip():
            obj = json.loads(line)
            if 'audio_filepath' in obj and isinstance(obj['audio_filepath'], str):
                if obj['audio_filepath'].startswith(old_prefix):
                    obj['audio_filepath'] = obj['audio_filepath'].replace(old_prefix, new_prefix, 1)
            data.append(obj)

data

[{'audio_filepath': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN622/SPK069YTNIN622F006.wav',
  'text': '연방 정부는 기존 (3)/(세) 가지 약물 조합을 하나의 약물로 대체하는 새로운 독극물 주사법을 지난해 승인했으며, 전날 (17)/(십 칠) 년 만에 연방 차원의 사형이 집행된 대니얼 루이스 리에게도 강력한 진정제인 펜토바르비탈이 주입됐습니다.'},
 {'audio_filepath': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN622/SPK069YTNIN622F002.wav',
  'text': '현지시간 (15)/(십 오) 일 (AP)/(에이 피) 통신 등 미 언론에 따르면 워싱턴 (DC)/(디 씨) 연방지방법원의 타냐 처칸 판사는 이날 사형 집행이 예정된 캔자스주 사형수 웨슬리 퍼키에 대한 사형을 금지하는 명령을 내렸습니다.'},
 {'audio_filepath': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN622/SPK069YTNIN622F007.wav',
  'text': '이에 따라 (17)/(십 칠) 일과 내달 (29)/(이십 구) 일에 각각 사형 집행이 예정된 더스틴 혼켄과 키스 넬슨의 사형 집행도 금지됐다고 로이터통신은 전했습니다.'},
 {'audio_filepath': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069Y

In [ ]:
news_preqa_data = []
for json_file in json_files:
    with open(json_file, 'r', encoding='utf-8') as f:
        items = json.load(f)
        base_name = os.path.splitext(os.path.basename(json_file))[0]
        audio_filepath = audio_prefix_map.get(base_name, None)
        if audio_filepath is None:
            print(f"No audio_filepath found for {base_name}")
            continue
        news_preqa_data.append({
            'audio_filepath': audio_filepath,
            'input' : None,
            'output': sentence_filter(raw_sentence=item['text'], mode='spelling')
        })

news_processed_data = []
for item in data:
    processed_item = {
        'audio_path': item['audio_filepath'], 
        'input' : None,
        'output': sentence_filter(raw_sentence=item['text'], mode='spelling')
    }
    news_processed_data.append(processed_item)

news_preqa_data

[{'filename': 'SPK020YTNSO380.json',
  'audio_filepath': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK020/SPK020YTNSO380/SPK020YTNSO380F003.wav',
  'data': [{'question': '첫 번째 수사본부장은 누구인가?', 'answer': '김 대령(수사본부장).'},
   {'question': '민간 검찰에 구속된 예비역 장교는 누구인가?', 'answer': '권 모 대령.'},
   {'question': '오늘 현역 김 모 대령에게 무슨 절차가 진행되는가?',
    'answer': '영장 실질 심사가 진행되며 구속 여부가 결정된다.'}]},
 {'filename': 'SPK038YTNPO867.json',
  'audio_filepath': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK038/SPK038YTNPO867/SPK038YTNPO867M006.wav',
  'data': [{'question': '김씨가 주장한 북한 공작원의 청와대 근무 기간은?', 'answer': '5~6년'},
   {'question': '현재 김씨는 어디에서 활동 중인가?', 'answer': '서울에서 한국 정보기관을 위해 일하고 있음'},
   {'question': '국가정보원은 김씨의 청와대 근무 주장에 대해 어떻게 답변했나요?',
    'answer': '주장이 사실무근이라고 밝힘'}]},
 {'filename': 'SPK066YTNIT298.json',
  'audio_filepath': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation

In [ ]:
import os
import glob
import json

preqa_dir = 'preQA_fixed/'
json_files = glob.glob(os.path.join(preqa_dir, '*.json'))

audio_prefix_map = {}
for item in data:
    if 'audio_filepath' in item and isinstance(item['audio_filepath'], str):
        wav_name = os.path.splitext(os.path.basename(item['audio_filepath']))[0]  
        prefix = wav_name[:-4]
        audio_prefix_map[prefix] = item['audio_filepath']

audio_prefix_map

{'SPK069YTNIN622': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN622/SPK069YTNIN622F003.wav',
 'SPK069YTNIN800': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN800/SPK069YTNIN800F002.wav',
 'SPK069YTNIN796': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN796/SPK069YTNIN796F001.wav',
 'SPK069YTNIN824': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN824/SPK069YTNIN824F003.wav',
 'SPK069YTNIN832': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN832/SPK069YTNIN832F001.wav',
 'SPK069YTNIN619': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN619/SPK069YTNIN619F001.wav',
 'SPK069YTNIN805': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_

In [ ]:
news_preqa_data = []
for json_file in json_files:
    with open(json_file, 'r', encoding='utf-8') as f:
        items = json.load(f)
        base_name = os.path.splitext(os.path.basename(json_file))[0]
        audio_filepath = audio_prefix_map.get(base_name, None)
        if audio_filepath is None:
            print(f"No audio_filepath found for {base_name}")
            continue
        news_preqa_data.append({
            'audio_filepath': audio_filepath,
            'input' : None,
            'output': sentence_filter(raw_sentence=item['text'], mode='spelling')
        })

news_processed_data = []
for item in data:
    processed_item = {
        'audio_path': item['audio_filepath'], 
        'input' : None,
        'output': sentence_filter(raw_sentence=item['text'], mode='spelling')
    }
    news_processed_data.append(processed_item)
news_preqa_data

[{'filename': 'SPK020YTNSO380.json',
  'audio_filepath': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK020/SPK020YTNSO380/SPK020YTNSO380F003.wav',
  'data': [{'question': '첫 번째 수사본부장은 누구인가?', 'answer': '김 대령(수사본부장).'},
   {'question': '민간 검찰에 구속된 예비역 장교는 누구인가?', 'answer': '권 모 대령.'},
   {'question': '오늘 현역 김 모 대령에게 무슨 절차가 진행되는가?',
    'answer': '영장 실질 심사가 진행되며 구속 여부가 결정된다.'}]},
 {'filename': 'SPK038YTNPO867.json',
  'audio_filepath': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK038/SPK038YTNPO867/SPK038YTNPO867M006.wav',
  'data': [{'question': '김씨가 주장한 북한 공작원의 청와대 근무 기간은?', 'answer': '5~6년'},
   {'question': '현재 김씨는 어디에서 활동 중인가?', 'answer': '서울에서 한국 정보기관을 위해 일하고 있음'},
   {'question': '국가정보원은 김씨의 청와대 근무 주장에 대해 어떻게 답변했나요?',
    'answer': '주장이 사실무근이라고 밝힘'}]},
 {'filename': 'SPK066YTNIT298.json',
  'audio_filepath': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation

In [4]:
news_processed_data = []
for item in data:
    processed_item = {
        'audio_path': item['audio_filepath'], 
        'input' : None,
        'output': sentence_filter(raw_sentence=item['text'], mode='spelling')
    }
    news_processed_data.append(processed_item)

news_processed_data

[{'audio_path': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN622/SPK069YTNIN622F006.wav',
  'input': None,
  'output': '연방 정부는 기존 3 가지 약물 조합을 하나의 약물로 대체하는 새로운 독극물 주사법을 지난해 승인했으며 전날 17 년 만에 연방 차원의 사형이 집행된 대니얼 루이스 리에게도 강력한 진정제인 펜토바르비탈이 주입됐습니다.'},
 {'audio_path': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN622/SPK069YTNIN622F002.wav',
  'input': None,
  'output': '현지시간 15 일 AP 통신 등 미 언론에 따르면 워싱턴 DC 연방지방법원의 타냐 처칸 판사는 이날 사형 집행이 예정된 캔자스주 사형수 웨슬리 퍼키에 대한 사형을 금지하는 명령을 내렸습니다.'},
 {'audio_path': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN622/SPK069YTNIN622F007.wav',
  'input': None,
  'output': '이에 따라 17 일과 내달 29 일에 각각 사형 집행이 예정된 더스틴 혼켄과 키스 넬슨의 사형 집행도 금지됐다고 로이터통신은 전했습니다.'},
 {'audio_path': '/home/nas4/DB/순천향대/Healthcare_SQA/138.뉴스_대본_및_앵커_음성_데이터/01-1.정식개방데이터/Validation/01.원천데이터/SPK069/SPK069YTNIN622/SPK069YT

In [ ]:
import aiohttp
import asyncio
import json
import os

from tqdm import tqdm
from transformers import AutoTokenizer

filenames = ['/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/train.scp', '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Validation/valid.scp']
all_data = []
for filename in filenames:
    with open(filename, 'r', encoding='utf-8') as f:
        for line in f:
            cleaned_line = line.strip()
            if cleaned_line:
                parts = cleaned_line.split('|', 1)
                all_data.append(parts)

offline_processed_data = []
for item in all_data:
    if len(item) == 2:
        offline_processed_data.append({
            "audio_path": item[0],
            'input' : None,
            "output": item[1]
        })

offline_processed_data

/home/DB/jhkim/speechllm/SpeechLLM/.venv/lib/python3.8/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


[{'audio_path': '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/doc/HB_0044/HB_0044-855-01-01-F-05-A.wav',
  'input': None,
  'output': '목에 침 삼킬 때 고통이 있나요?'},
 {'audio_path': '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/doc/HB_0044/HB_0044-894-01-01-F-05-A.wav',
  'input': None,
  'output': '술은 가볍게 하는 편인가요?'},
 {'audio_path': '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/doc/HB_0044/HB_0044-745-01-01-F-05-A.wav',
  'input': None,
  'output': '현재 체중 변화가 심한 가요?'},
 {'audio_path': '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/doc/HB_0044/HB_0044-23-01-01-F-05-A.wav',
  'input': None,
  'output': '피로감이 느껴지시면 말해주세요.'},
 {'audio_path': '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/doc/HB_0044/HB_0044-841-01-01-F-05-A.wav',
  'input': None,
  'output': '몸살 기운은 없나요?'},
 {'audio_path': '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/doc/HB_0044/HB_0044-531-01-01-F-05-A.wav',
  'input': None,
  'output': '지금까지 약은 계속

In [ ]:
import json

file_path = 'cleaned_results.json'

with open(file_path, 'r', encoding='utf-8') as f:
    datas = json.load(f)

large_med_processed_data = []
idx = 0
for item in datas:
    processed_item = {
        "audio_path": None,
        'input': sentence_filter(raw_sentence=item['generated_text'], mode='spelling'), 
        'output': sentence_filter(raw_sentence=item['answer'], mode='spelling')
    }
    large_med_processed_data.append(processed_item)

large_med_processed_data

[{'audio_path': None,
  'input': '성병이 성적 접촉을 통해 전파되는 질병인지 그리고 치료를 받지 않으면 심각한 합병증을 유발할 수 있는가?',
  'output': '성병은 성적 접촉을 통해 전파되는 전염성 질병입니다.성병의 감염자는 치료 없이도 자연스럽게 회복되기도 하지만 성적인 접촉을 통해 감염이 확산될 수도 있습니다.성병은 치료하지 않으면 심각한 합병증을 유발할 수 있습니다. 특히 매독이나 헤르페스 에이즈 등의 성병은 치료가 매우 중요합니다. 조기에 치료를 받으면 대부분의 환자는 완치될 수 있지만 치료를 받지 않은 환자들의 경우 일부 장기에 염증이나 마비 증상이 나타날 수 있습니다. 성병은 일상 생활에서도 전파될 수 있으므로 예방이 매우 중요합니다.'},
 {'audio_path': None,
  'input': '성병을 주로 어떻게 전파되는지 알고 싶습니다.',
  'output': '성병은 성 접촉을 통해 전파되는 바이러스 감염 질환입니다. 일반적으로 성기나 항문을 통해 바이러스가 직접 또는 간접적으로 성병 바이러스로 감염됩니다.성병 바이러스 감염은 성관계 혈액 접촉 등 성 접촉을 통해 전파될 수 있습니다. 특히 자궁경부암 예방 접종을 한 경우 자궁경부 세포진 검사를 통해 성병 바이러스가 발견되면 성 접촉을 통해 전파될 가능성이 높습니다. 감염된 성병은 감염 부위에 따라 다양한 증상을 보일 수 있습니다. 이는 성병의 종류에 따라 다를 수 있으며 특히 헤르페스 바이러스 감염은 다양한 증상을 나타냅니다.따라서 성병은 주로 성 접촉을 통해 전파되는 질병이며 적절한 예방 조치를 취하는 것이 중요합니다. 성병 감염을 예방하기 위해서는 정기적인 검사와 의사의 지도를 받는 것이 필요합니다.'},
 {'audio_path': None,
  'input': '"성병이 성 접촉을 통해 전파되는 질환인지 어떻게 예방하고 치료할 수 있는지 알고 싶습니다."',
  'output': '성병은 성 접촉을 통해 전파되는 질환으로 치료 가능합니다. 성병

In [ ]:
import json

file_path = 'Asan-AMC-Healthinfo.json'

with open(file_path, 'r', encoding='utf-8') as f:
    data = json.load(f)

idx = 0

Asan_processed_data = []
for item in data:
    processed_item = {
        "audio_path": None,
        'input': sentence_filter(raw_sentence=item['instruction'], mode='spelling'), 
        'output': sentence_filter(raw_sentence=item['output'], mode='spelling')
    }
    Asan_processed_data.append(processed_item)

Asan_processed_data

[{'audio_path': None,
  'input': '경피적 간담도조영술의 정의에 대해서 설명해주세요.',
  'output': '경피적 간담도조영술은 담도에 조영제를 직접 투여한 후 X선 촬영을 하여 담도의 구조와 형태 비정상적인 병변을 관찰하기 위한 검사입니다. 주로 간이식 수술 시 삽입한 담도 배액관을 통해 조영함으로써 영상을 통해 관찰할 수 있다는 장점이 있습니다. 시술 과정에서 소량의 방사선에 노출됩니다.'},
 {'audio_path': None,
  'input': '경피적 간담도조영술의 준비사항은 무엇인가요?',
  'output': '시술 전 4시간 금식합니다. 당뇨로 인슐린을 투약 중인 경우 혈압강하제나 혈전 용해제를 투약 중인 경우 신장질환이 있는 경우 조영제 등의 약물 부작용 과거력이 있는 경우 심장질환이나 폐질환 알레르기질환을 보유한 경우 시술 전 반드시 의료진에게 해당사항에 대해 알려주어야 합니다. 임산부의 검사를 진행할 경우 태아에게 방사선 피폭에 따른 영향이 있을 수 있으므로 검사 전 임신 여부 및 가능성에 대해 의료진에게 알리도록 합니다. 이전의 검사 시 조영제 알레르기 반응이 있었거나 평소 음식이나 특정 물질 또는 약물에 대한 알레르기 반응이 있다면 미리 알리도록 합니다. 시술 전 초음파 CT MRI 등을 이용하여 간담도의 상태를 확인합니다.'},
 {'audio_path': None,
  'input': '경피적 간담도조영술의 적응증에 대해서 설명해주세요.',
  'output': '간기능 수치 이상 황달 상복부 통증 소화불량 등의 담도계 이상 증상이 있을 때 시행하게 됩니다.'},
 {'audio_path': None,
  'input': '경피적 간담도조영술의 검사시술수술 방법은 무엇인가요?',
  'output': '1. 담도에 삽입된 배액관의 위치를 영상으로 확인합니다.2. 식염수로 배액관의 개통 여부를 확인합니다.3. 배액관을 통하여 조영제를 주입하여 담도의 모습이나 폐쇄 유무 합병증 유무 등을 확인한 후 시술

In [8]:
import json

merged_data = offline_processed_data + large_med_processed_data + Asan_processed_data

with open("train_data.json", "w", encoding="utf-8") as f:
    json.dump(merged_data, f, ensure_ascii=False, indent=2)

print('train 성공')

with open("validation_data.json", "w", encoding="utf-8") as f:
    json.dump(news_processed_data, f, ensure_ascii=False, indent=2)
    
print('val 성공')


train 성공
val 성공


In [11]:
with open("train_data.json", "r", encoding="utf-8") as f:
    data = json.load(f)

print("상위 10개 샘플:")
for i, item in enumerate(data[:10], 1):
    print(f"{i}: {item}")


상위 10개 샘플:
1: {'audio_path': '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/doc/HB_0044/HB_0044-855-01-01-F-05-A.wav', 'input': None, 'output': '목에 침 삼킬 때 고통이 있나요?'}
2: {'audio_path': '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/doc/HB_0044/HB_0044-894-01-01-F-05-A.wav', 'input': None, 'output': '술은 가볍게 하는 편인가요?'}
3: {'audio_path': '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/doc/HB_0044/HB_0044-745-01-01-F-05-A.wav', 'input': None, 'output': '현재 체중 변화가 심한 가요?'}
4: {'audio_path': '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/doc/HB_0044/HB_0044-23-01-01-F-05-A.wav', 'input': None, 'output': '피로감이 느껴지시면 말해주세요.'}
5: {'audio_path': '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/doc/HB_0044/HB_0044-841-01-01-F-05-A.wav', 'input': None, 'output': '몸살 기운은 없나요?'}
6: {'audio_path': '/home/nas4/DB/AI_Hub_비대면진료/비대면_진료를_위한_의료진_및_환자_음성/Training/doc/HB_0044/HB_0044-531-01-01-F-05-A.wav', 'input': None, 'output': '지금까지 약은 계속 드시고 계